# Multiple filter technique

An alternative to the moving window method is the multiple filter technique. Instead of moving a window in the time domain, a window is moved in the frequency domain. Of course, a window in the frequency domain is a filter, and hence the name of the method. Let $H_k(\omega,\omega_k)$ be the transfer function of the $k$-th filter centered on frequency $\omega_k$. Applying the filter involves multiplication of the filter transfer function with the Fourier transform of the time signal and then performing an inverse Fourier transform:
\begin{align}
f_k(t) = \int_{-\infty}^\infty\,H_k(\omega,\omega_k)F(\omega)\exp(i\omega t)\frac{d\omega}{2\pi} \,.
\end{align}
Basically, one could plot the resulting time series against the associated center frequency of the filter. However, $f_k(t)$ can also assume negative values. It would be better to plot the envelope of $f_k(t)$.

### The analytic signal
This can be obtained by constructing the analytic signal $z_k(t)$ of $f_k(t)$. It is a complex
signal whose real part is the original signal and whose imaginary part is its Hilbert transform. Its absolute
value is the envelope or instantaneous amplitude and its phase is the instantaneous phase:
\begin{align}
z_k(t) = a_k(t)\exp(i\Phi_k(t)) = f_k(t)+iq_k(t) \ \mathrm{with}\ q_k(t) = HT\{f_k(t)\}\,,
\end{align}
and
\begin{align}
a_k(t) = \sqrt{f_k(t)^2+q_k(t)^2},\ \Phi_k(t) = \arctan\left(\frac{q_k(t)}{f_k(t)}\right) \,.
\end{align}

The Hilbert transform can again easily be obtained because its Fourier transform is:
\begin{align}
Q_k(\omega) = i\,\mathrm{sign}(\omega)F_k(\omega)\,.
\end{align}
where $F_k(\omega)$ is the Fourier transform of $f_k(t)$. Inverse Fourier transform of $Q_k(\omega)$ gives the Hilbert transform of $f_k(t)$.

### Work flow
So the work flow of the multiple filter technique is as follows:
1. Compute Fourier transform of $f(t)$: $F(\omega)$.
2. Multiply $F(\omega)$ with bandpass filters $H_k(\omega,\omega_k)$ to obtain $F_k(\omega)$.
3. Compute Fourier transform of the Hilbert transform: $Q_k(\omega)=iF_k(\omega)$.
4. Transform both back to the time domain.
5. Calculate the instantaneous amplitude $a_k(t)$ and phase $\Phi_k(t)$.
6. Plot $a_k(t)$ in the time-frequency plane.

### Gaussian filters
One frequently made choice for the bandpass filters is a Gaussian function of the form:
\begin{align}
H_k(\omega,\omega_k) = e^{-\alpha\left(\frac{\omega-\omega_k}{\omega_k}\right)^2}
\end{align}
with inverse Fourier transform (impulse response):
\begin{align}
h_k(t) = \frac{\sqrt{\pi}\omega_k}{2\alpha}e^{-\frac{\omega_k^2t^2}{4\alpha}}\cos\omega_k t \,.
\end{align}
This Fourier transform pair demonstrates a fundamental property of spectral analysis:
Choosing $\alpha$ large gives a very narrow-banded filter but a very
long impulse response. Choosing $\alpha$ small gives a wide-banded filter but a very short 
impulse response. This is an expression of the uncertainty principle. If the frequency of a signal
is known very well, the signal is distributed over time. On the other hand, an impulse in the time domain has
a constant spectrum, i.e. the frequency is entirely unknown. In quantum mechanics, there is the energy-time
uncertainty relation, where energy $E=\hbar\omega$.

### Time and frequency resolution
The Gaussian Fourier transform pair has a special property. If we measure the duration of the impulse response by
\begin{align}
D_t^2 = \int_{-\infty}^\infty t^2 |h(t)|^2 dt
\end{align}
and the spread of the filter transfer function by
\begin{align}
D_\omega^2 = \int_{-\infty}^\infty \omega^2 |H(\omega)|^2 \frac{d\omega}{2\pi}\,,
\end{align}
then the product
\begin{align}
D_t D_\omega \ge \frac{1}{2} \,.
\end{align}
For the Gaussian filter, equality holds. Hence, the Gaussian filter is the one with the
best compromise between bandwidth and duration.

In [ ]:
# Preparation: load packages
%matplotlib inline
from obspy.core import read
from obspy.core import UTCDateTime
import numpy as np
import matplotlib.pylab as plt
from setupFigure import SetupFigure

In [ ]:
def multipleFilterAnalysis(data, alfa, cfreq, dt, ndec):
    """
    Perform a multiple filter analysis of data.
    :param data:  Array of detrended and demeaned data 
    :param alfa:  Width parameter of Gaussian bandpass filter
    :param cfreq: Array of center frequencies of Gaussian filter
    :param dt: sampling interval of data
    :param ndec: decimation factor for instantaneous amplitude output
    """
    nd = len(data)
    ftd = np.fft.rfft(data,nd)                   # Fourier transform of entire data set (pos. freq.)
    freq = np.fft.rfftfreq(nd,dt)                # Fourier frequencies (positive frequencies)
    jf = 0                                       # center frequency counter
    mfa = np.zeros((len(cfreq),nd//ndec))        # numpy array for MFA result
    for cf in cfreq:
        hg = np.exp(-alfa*((freq-cf)/cf)**2)     # Gaussian filter (use f instead of omega here)
        fk = hg*ftd                              # multiply FT of data with filter
        qk = 1j*fk                               # FT of Hilbert transform of filtered data
        ftk = np.fft.irfft(fk)                   # filtered data
        qtk = np.fft.irfft(qk)                   # Hilbert transform of filtered data
        at = np.sqrt(ftk**2+qtk**2)              # instantaneous amplitude
        mfa[jf,:] = at[0:nd:ndec]                # store decimated original result
        jf = jf+1                                # increase center frequency count
    return mfa

In [ ]:
def normalizeMFT(mfa, mode = 'full', exp = 0.5):
    """
    Normalize the result of the mutiple filtering operation.
    :param mfa: array with envelopes versus frequency (mfa(f,t))
    :param mode: normalization mode: 
                 if 'time': normalize timewise
                 if 'freq': normalize frequencywise
                 else: normalize to absolute maximum of entire array
    :param exp:  exponent for modifying envelope using a power
    """
    nf, nt = mfa.shape
    if mode == 'freq':
        for jf in range(0,nf):
            mfamax = np.amax(mfa[jf,:])
            mfa[jf,:] = np.power(mfa[jf,:]/mfamax+1.e-10, exp)          
    elif mode == 'time':
        for jt in range(0,nt):
            mfamax = np.amax(mfa[:,jt])
            mfa[:,jt] = np.power(mfa[:,jt]/mfamax+1.e-10, exp)
    else:        
            mfamax = np.amax(mfa)
            mfa = np.power(mfa/mfamax+1.e-10, exp)
    #        mfa = np.log10(mfa/mfamax+1.e-10)
    return mfa

In [ ]:
record = '1400'                                     # either use record starting at 1300 or 1400
datapath = 'geo2.' + record+ '.HHZ'

if record =='1300':
    stime = UTCDateTime('2013-01-23 13:16:00Z')      # use record starting at 1300
    etime = UTCDateTime('2013-01-23 13:25:00Z')
    ttitle = ', depth: 36.5 m'
else:
    stime = UTCDateTime('2013-01-23 14:14:00Z')      # use record starting at 1400 (14:14-14:23)
    etime = UTCDateTime('2013-01-23 14:23:00Z')
    ttitle = ', depth: 56.5 m'
    
st = read(datapath)                                  # read file using obspy read

st.trim(stime,etime)      # trim data stream to desired start and end time
st.detrend('linear')      # do a linear detrending
st.detrend('demean')      # subtract mean value

In [ ]:
tr = st[0]                # extract first trace from stream (there is only one)
tr.plot()                 # plot trace

In [ ]:
# prepare multiple filtering
alfa = 10.                                     # filter width parameter
nd = tr.stats.npts                                # number of samples in time series
dt = tr.stats.delta                               # sampling interval
fmax = 1./(2.*dt)                                 # Nyquist frequency
cfreq = np.linspace(1., fmax, 1000)               # array of filter center frequencies
freq = np.fft.rfftfreq(nd, dt)                    # Fourier frequencies

In [ ]:
ndec = 100                                        # decimation factor for envelope
mfa = multipleFilterAnalysis(tr.data, alfa, cfreq, dt, ndec)

In [ ]:
mfa = normalizeMFT(mfa, mode='full', exp = 0.5)

In [ ]:
# plot the result
extent = (0., nd*dt, fmax, 1.)                         # extent of matrix in true time and frequency
fig1, ax1 = SetupFigure(15, 6, "Time [s]", "Center frequency [Hz]", "Multiple filter analysis", 14)
ax1.imshow(mfa, extent = extent, aspect=1)

In [ ]:
# plot Gaussian filter
cf = 30
fig2, ax2 = SetupFigure(15, 6, "Center frequency [Hz]", "Amplitude", "Gaussian filter", 14)
arg = (freq-cf)/cf
hg = np.exp(-alfa*((freq-cf)/cf)**2)     # Gaussian filter (use f instead of omega here)
ax2.plot(freq, hg)

In [ ]:
# plot filter response
fig3, ax3 = SetupFigure(15, 6, "Time [s]", "Amplitude", "Filter response", 14)
wk = cf*2.*np.pi
ts = np.linspace(-2.5,2.5,5000)
hres = wk/np.sqrt(np.pi*alfa)*np.exp(-(0.25*(wk*ts)**2/alfa))*np.cos(wk*ts) 
ax3.plot(ts, hres)

# Tasks

1. Study the effect of $\alpha$ on the result of the multiple filtering and on the form of the filter impulse response.
2. Up to which value of $\alpha$ do you need to go to achieve a frequency resolution comparable to the moving window method
3. Think about the numerical effort of MFT in comparison with the moving window technique.
4. Try different scalings of the MFT result using different powers and also the logarithm.
5. Try timewise and frequenc-wise normalization.
6. Do you have some ideas why the results look different? What role play scaling and normalization? 
7. Plot the Gaussian filter transfer function for different values of $\alpha$.
8. Plot the filter responses for different values of $\alpha$.